In [212]:
import os
import polars as pl
pl.Config(tbl_rows=100)
from src.najdi_rok import najdi_rok
from src.pocet_stran import pocet_stran

In [214]:
def bezbordelu(text):
    if not text:  # Check if string is empty
        return text
        
    if not text[-1].isalnum():  # Check if last character is not a letter
        return text[:-1].strip()
    
    return text

In [216]:
# df = pl.read_parquet(os.path.join("data","cnb_ceska_proza.parquet")).rename({'autorstvo_kod':'100_7'})
# df = pl.concat([df, pl.read_parquet(os.path.join("data","cnb_ceska_poezie.parquet"))])
# spisovatelstvo = list(set(df.select(pl.col('100_7')).drop_nulls().to_series().to_list()))
df = pl.read_parquet(os.path.join("data/cnb_sloupce","100.parquet"))
# df = df.filter(pl.col("100_7").is_in(spisovatelstvo))
aut = pl.read_parquet(os.path.join("data","aut_vyber.parquet")).explode("370_c").filter(pl.col("370_c").str.contains("Česk")).explode("100_7").select(["100_7","374_a","375_a","678_a"])
df = df.join(aut, left_on="100_7", right_on="100_7", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","008.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","245.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","300.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","655.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","700.parquet")), left_on="001", right_on="001", how="left")
df = df.with_columns(pl.col('008').map_elements(najdi_rok, return_dtype=int).alias('rok'))
df = df.with_columns(pl.col('300_a').map_elements(najdi_rok, return_dtype=int).alias('stran'))
df = df.with_columns(pl.col('245_a').map_elements(bezbordelu))

C:\Users\micha\AppData\Local\Temp\ipykernel_17068\2279827255.py:15: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
  df = df.with_columns(pl.col('245_a').map_elements(bezbordelu))


In [218]:
df = df.filter(pl.col("rok") >= 1800)

In [219]:
df.group_by(["100_a","100_7"]).len().sort(by="len",descending=True).head(n=100)

shape: (100, 3)
┌─────────────────────────────────┬───────────────┬──────┐
│ 100_a                           ┆ 100_7         ┆ len  │
│ ---                             ┆ ---           ┆ ---  │
│ str                             ┆ str           ┆ u32  │
╞═════════════════════════════════╪═══════════════╪══════╡
│ Rillich, Ivan,                  ┆ jx20060515016 ┆ 2987 │
│ Prášil, Petr,                   ┆ jx20050830020 ┆ 2370 │
│ Unger, Gert F.,                 ┆ jn20001103529 ┆ 1672 │
│ Toman, Petr,                    ┆ xx0021455     ┆ 1308 │
│ Dvořák, Antonín,                ┆ jn19981000826 ┆ 1239 │
│ Vandenberg, Patricia,           ┆ jn20000810141 ┆ 1180 │
│ Němcová, Božena,                ┆ jk01083016    ┆ 1130 │
│ Jirásek, Alois,                 ┆ jk01051816    ┆ 1110 │
│ Smetana, Bedřich,               ┆ jk01120043    ┆ 1080 │
│ Kurc, David,                    ┆ jx20040720153 ┆ 932  │
│ Čapek, Karel,                   ┆ jk01021023    ┆ 893  │
│ Kincl, Milan,                   ┆ jo20010084283 ┆ 834  │
│ Verne, Jules,                   ┆ jn19990008769 ┆ 782  │
│ Suttner, Jiří                   ┆ jo2005273951  ┆ 780  │
│ Vedral, Jiří,                   ┆ mzk2003169026 ┆ 750  │
│ Hašler, Karel,                  ┆ jk01040136    ┆ 721  │
│ Dark, Jason,                    ┆ jn20000810032 ┆ 721  │
│ Neruda, Jan,                    ┆ jk01083209    ┆ 656  │
│ Courths-Mahler, Hedwig,         ┆ jn19990001513 ┆ 654  │
│ Shakespeare, William,           ┆ jn19981002129 ┆ 635  │
│ Ebr, Josef                      ┆ jx20110607004 ┆ 621  │
│ Lada, Josef,                    ┆ jk01071364    ┆ 608  │
│ Erben, Karel Jaromír,           ┆ jk01030532    ┆ 564  │
│ Kirby, John                     ┆ jx20040611003 ┆ 559  │
│ Vrchlický, Jaroslav,            ┆ jk01151037    ┆ 527  │
│ Janáček, Leoš,                  ┆ jk01050745    ┆ 526  │
│ Javořická, Vlasta,              ┆ jk01051344    ┆ 472  │
│ Miler, Zdeněk,                  ┆ jk01081695    ┆ 455  │
│ Thomayer, Karel                 ┆ jx20040906013 ┆ 435  │
│ Komenský, Jan Amos,             ┆ jk01061444    ┆ 433  │
│ Mucha, Alfons,                  ┆ jk01082370    ┆ 428  │
│ May, Karl,                      ┆ jn19990005499 ┆ 423  │
│ Drahoňovský, Milan,             ┆ jo20010087090 ┆ 414  │
│ Rais, Karel Václav,             ┆ jk01101955    ┆ 407  │
│ Masaryk, Tomáš Garrigue,        ┆ jk01080472    ┆ 406  │
│ Tyl, Josef Kajetán,             ┆ jk01140553    ┆ 406  │
│ Tolstoj, Lev Nikolajevič,       ┆ jn19981002230 ┆ 404  │
│ Dumas, Alexandre,               ┆ jn19990001907 ┆ 401  │
│ Čech, Svatopluk,                ┆ jk01021137    ┆ 388  │
│ Jankovec, Jaroslav,             ┆ jn20000401191 ┆ 382  │
│ Ropek, Rudolf,                  ┆ jx20041020017 ┆ 381  │
│ Arbes, Jakub,                   ┆ jk01010356    ┆ 378  │
│ Beneš, Jára,                    ┆ jn19990209042 ┆ 376  │
│ Morávek, Jiří,                  ┆ jx20040914014 ┆ 372  │
│ Christie, Agatha,               ┆ jn19981000482 ┆ 372  │
│ Mácha, Karel Hynek,             ┆ jk01072915    ┆ 372  │
│ Stelibský, Josef,               ┆ jn19990009996 ┆ 372  │
│ Martinů, Bohuslav,              ┆ jk01080381    ┆ 365  │
│ Imlauf, Lubomír,                ┆ jo2005274103  ┆ 356  │
│ Wagner, Jan Eduard,             ┆ jk01151315    ┆ 356  │
│ Matějíček, Aleš                 ┆ jx20040907013 ┆ 355  │
│ Zeyer, Julius,                  ┆ jk01152552    ┆ 355  │
│ Clifton, Léon                   ┆ xx0111518     ┆ 353  │
│ Lenin, Vladimir Il‘jič,         ┆ jn19981001737 ┆ 348  │
│ Hrubín, František,              ┆ jk01042920    ┆ 340  │
│ Sváček, Libor,                  ┆ xx0011154     ┆ 337  │
│ Pittnerová, Vlasta,             ┆ jk01093291    ┆ 337  │
│ Šulc, Petr,                     ┆ jn20011018797 ┆ 329  │
│ Strong, Pitt,                   ┆ jo2005267810  ┆ 323  │
│ Batěk, Alexandr,                ┆ jk01011106    ┆ 321  │
│ Šváb-Malostranský, Josef,       ┆ jk01131780    ┆ 318  │
│ Birkner-Mahler, Frieda,         ┆ jn20000600873 ┆ 318  │
│ Scott, William,              

In [220]:
nechcemejetam = [
    "jn19990008769",
    "jx20060515016",
    "jn19981002230",
    "jn19981001737",
    "jn19990210182",
    "jn19990001842",
    "jn19990002786",
    "jn19990004346",
    "jn20020721077",
    "jn19990210513",
    "jn19990005488",
    "jo20000080627",
    "jn19990000171",
    "jn20001005715",
    "jn19981002409",
    "jn20000810141",
    "jn19981002129",
    "jn20001103529",
    "jn20000810032",
    "jn19990001513",
    "jx20040611003",
    "jn19990005499",
    "jn19981002230",
    "jn19990001907",
    "jo2005267810",
    "jo20241218643"
]

In [221]:
df = df.filter(~pl.col("100_7").is_in(nechcemejetam))

In [222]:
df.group_by("rok").len().sort(by="rok")

shape: (226, 2)
┌──────┬───────┐
│ rok  ┆ len   │
│ ---  ┆ ---   │
│ i64  ┆ u32   │
╞══════╪═══════╡
│ 1800 ┆ 3     │
│ 1801 ┆ 52    │
│ 1802 ┆ 52    │
│ 1803 ┆ 52    │
│ 1804 ┆ 65    │
│ 1805 ┆ 55    │
│ 1806 ┆ 38    │
│ 1807 ┆ 44    │
│ 1808 ┆ 53    │
│ 1809 ┆ 41    │
│ 1810 ┆ 52    │
│ 1811 ┆ 35    │
│ 1812 ┆ 57    │
│ 1813 ┆ 58    │
│ 1814 ┆ 59    │
│ 1815 ┆ 65    │
│ 1816 ┆ 84    │
│ 1817 ┆ 117   │
│ 1818 ┆ 118   │
│ 1819 ┆ 128   │
│ 1820 ┆ 160   │
│ 1821 ┆ 146   │
│ 1822 ┆ 151   │
│ 1823 ┆ 115   │
│ 1824 ┆ 123   │
│ 1825 ┆ 117   │
│ 1826 ┆ 138   │
│ 1827 ┆ 116   │
│ 1828 ┆ 136   │
│ 1829 ┆ 144   │
│ 1830 ┆ 163   │
│ 1831 ┆ 183   │
│ 1832 ┆ 142   │
│ 1833 ┆ 126   │
│ 1834 ┆ 129   │
│ 1835 ┆ 178   │
│ 1836 ┆ 190   │
│ 1837 ┆ 138   │
│ 1838 ┆ 137   │
│ 1839 ┆ 149   │
│ 1840 ┆ 183   │
│ 1841 ┆ 166   │
│ 1842 ┆ 188   │
│ 1843 ┆ 214   │
│ 1844 ┆ 213   │
│ 1845 ┆ 180   │
│ 1846 ┆ 185   │
│ 1847 ┆ 197   │
│ 1848 ┆ 218   │
│ 1849 ┆ 210   │
│ …    ┆ …     │
│ 1976 ┆ 4235  │
│ 1977 ┆ 4202  │
│ 1978 ┆ 4170  │
│ 1979 ┆ 4376  │
│ 1980 ┆ 4475  │
│ 1981 ┆ 4294  │
│ 1982 ┆ 4459  │
│ 1983 ┆ 4344  │
│ 1984 ┆ 4559  │
│ 1985 ┆ 4299  │
│ 1986 ┆ 4558  │
│ 1987 ┆ 4557  │
│ 1988 ┆ 4659  │
│ 1989 ┆ 4751  │
│ 1990 ┆ 4996  │
│ 1991 ┆ 5647  │
│ 1992 ┆ 6486  │
│ 1993 ┆ 8058  │
│ 1994 ┆ 8256  │
│ 1995 ┆ 9069  │
│ 1996 ┆ 9004  │
│ 1997 ┆ 10381 │
│ 1998 ┆ 10702 │
│ 1999 ┆ 11731 │
│ 2000 ┆ 13003 │
│ 2001 ┆ 12379 │
│ 2002 ┆ 12597 │
│ 2003 ┆ 13367 │
│ 2004 ┆ 13702 │
│ 2005 ┆ 14014 │
│ 2006 ┆ 14352 │
│ 2007 ┆ 15383 │
│ 2008 ┆ 17029 │
│ 2009 ┆ 15248 │
│ 2010 ┆ 16109 │
│ 2011 ┆ 15361 │
│ 2012 ┆ 14917 │
│ 2013 ┆ 14547 │
│ 2014 ┆ 15103 │
│ 2015 ┆ 14820 │
│ 2016 ┆ 14028 │
│ 2017 ┆ 13936 │
│ 2018 ┆ 14032 │
│ 2019 ┆ 13837 │
│ 2020 ┆ 12383 │
│ 2021 ┆ 12989 │
│ 2022 ┆ 13325 │
│ 2023 ┆ 11893 │
│ 2024 ┆ 10099 │
│ 2025 ┆ 181   │
└──────┴───────┘

In [223]:
df.group_by("100_a").len().sort(by="len",descending=True).head(100)

shape: (100, 2)
┌───────────────────────────┬──────┐
│ 100_a                     ┆ len  │
│ ---                       ┆ ---  │
│ str                       ┆ u32  │
╞═══════════════════════════╪══════╡
│ Prášil, Petr,             ┆ 2370 │
│ Toman, Petr,              ┆ 1314 │
│ Dvořák, Antonín,          ┆ 1274 │
│ Němcová, Božena,          ┆ 1130 │
│ Jirásek, Alois,           ┆ 1110 │
│ Smetana, Bedřich,         ┆ 1080 │
│ Kurc, David,              ┆ 932  │
│ Čapek, Karel,             ┆ 900  │
│ Kincl, Milan,             ┆ 834  │
│ Suttner, Jiří             ┆ 780  │
│ Vedral, Jiří,             ┆ 755  │
│ Hašler, Karel,            ┆ 721  │
│ Neruda, Jan,              ┆ 656  │
│ Ebr, Josef                ┆ 621  │
│ Lada, Josef,              ┆ 610  │
│ Erben, Karel Jaromír,     ┆ 564  │
│ Vrchlický, Jaroslav,      ┆ 527  │
│ Janáček, Leoš,            ┆ 526  │
│ Javořická, Vlasta,        ┆ 472  │
│ Miler, Zdeněk,            ┆ 455  │
│ Thomayer, Karel           ┆ 435  │
│ Komenský, Jan Amos,       ┆ 433  │
│ Mucha, Alfons,            ┆ 428  │
│ Drahoňovský, Milan,       ┆ 414  │
│ Rais, Karel Václav,       ┆ 407  │
│ Masaryk, Tomáš Garrigue,  ┆ 406  │
│ Tyl, Josef Kajetán,       ┆ 406  │
│ Čech, Svatopluk,          ┆ 396  │
│ Jankovec, Jaroslav,       ┆ 382  │
│ Ropek, Rudolf,            ┆ 381  │
│ Arbes, Jakub,             ┆ 378  │
│ Beneš, Jára,              ┆ 376  │
│ Morávek, Jiří,            ┆ 372  │
│ Christie, Agatha,         ┆ 372  │
│ Mácha, Karel Hynek,       ┆ 372  │
│ Stelibský, Josef,         ┆ 372  │
│ Martinů, Bohuslav,        ┆ 365  │
│ Matějíček, Aleš           ┆ 358  │
│ Imlauf, Lubomír,          ┆ 356  │
│ Wagner, Jan Eduard,       ┆ 356  │
│ Zeyer, Julius,            ┆ 355  │
│ Clifton, Léon             ┆ 353  │
│ Hrubín, František,        ┆ 340  │
│ Sváček, Libor,            ┆ 337  │
│ Pittnerová, Vlasta,       ┆ 337  │
│ Šulc, Petr,               ┆ 331  │
│ Batěk, Alexandr,          ┆ 321  │
│ Birkner-Mahler, Frieda,   ┆ 318  │
│ Šváb-Malostranský, Josef, ┆ 318  │
│ Scott, William,           ┆ 317  │
│ Mach, Pravoslav,          ┆ 316  │
│ Světlá, Karolina,         ┆ 315  │
│ Ježek, Jaroslav,          ┆ 315  │
│ Žáček, Jiří,              ┆ 312  │
│ Kavale, Jan,              ┆ 311  │
│ Baar, Jindřich Šimon,     ┆ 310  │
│ Petiška, Eduard,          ┆ 301  │
│ Seifert, Jaroslav,        ┆ 299  │
│ Foerster, Josef Bohuslav, ┆ 299  │
│ Vondruška, Vlastimil,     ┆ 299  │
│ Suk, Josef,               ┆ 298  │
│ Nezval, Vítězslav,        ┆ 297  │
│ Fibich, Zdeněk,           ┆ 294  │
│ Machar, Josef Svatopluk,  ┆ 293  │
│ Váchal, Josef,            ┆ 290  │
│ Hálek, Vítězslav,         ┆ 290  │
│ London, Jack,             ┆ 287  │
│ Havlíček Borovský, Karel, ┆ 286  │
│ Vrba, Jan,                ┆ 285  │
│ Hašek, Jaroslav,          ┆ 281  │
│ Gollwell, John,           ┆ 280  │
│ Pospíšilová, Zuzana,      ┆ 277  │
│ Tichý, František Alois,   ┆ 271  │
│ Bezruč, Petr,             ┆ 270  │
│ Dvořák, Jiří,             ┆ 269  │
│ Wallace, Edgar,           ┆ 268  │
│ Nejedlý, Zdeněk,          ┆ 267  │
│ Beneš Třebízský, Václav,  ┆ 263  │
│ Herrmann, Ignát,          ┆ 263  │
│ Majerová, Marie,          ┆ 263  │
│ David, Petr,              ┆ 262  │
│ Vojkovský, Rostislav,     ┆ 262  │
│ Fučík, Julius,            ┆ 259  │
│ Brezina, Thomas,          ┆ 258  │
│ Beneš, Edvard,            ┆ 257  │
│ Balzac, Honoré de,        ┆ 253  │
│ Šplíchal, Antonín,        ┆ 253  │
│ Dobrovolný, Bohumil,      ┆ 249  │
│ Foglar, Jaroslav,         ┆ 249  │
│ Kožík, František,         ┆ 249  │
│ Krob, Miroslav,           ┆ 248  │
│ Čtvrtek, Václav,          ┆ 247  │
│ Mozart, Wolfgang Amadeus, ┆ 244  │
│ Klostermann, Karel,       ┆ 243  │
│ Steiner, Rudolf,          ┆ 243  │
│ Grey, Zane,               ┆ 242  │
│ Čapek, Josef,             ┆ 242  │
│ Svoboda, F. X.,           ┆ 240  │
│ Selucký, Daniel           ┆ 239  │
│ Brázda, Petr              ┆ 239  │
└───────────────────────────┴──────┘

In [224]:
df.filter(pl.col("100_a") == "Mark, William,")

shape: (0, 66)
┌──────────┬───────┬───────┬───────────┬───┬───────────┬───────────┬─────┬───────┐
│ 100_ind1 ┆ 100_a ┆ 100_7 ┆ 100_4     ┆ … ┆ 700_5     ┆ 700_g     ┆ rok ┆ stran │
│ ---      ┆ ---   ┆ ---   ┆ ---       ┆   ┆ ---       ┆ ---       ┆ --- ┆ ---   │
│ str      ┆ str   ┆ str   ┆ list[str] ┆   ┆ list[str] ┆ list[str] ┆ i64 ┆ i64   │
╞══════════╪═══════╪═══════╪═══════════╪═══╪═══════════╪═══════════╪═════╪═══════╡
└──────────┴───────┴───────┴───────────┴───┴───────────┴───────────┴─────┴───────┘

In [225]:
len(df)

800914

In [226]:
df = df.explode("100_4").filter(pl.col("100_4") == "aut")

In [227]:
len(df)

680289

In [228]:
df = df.unique(subset=["100_a","245_a"])

In [229]:
len(df)

535900

In [230]:
len(list(set(df.select(pl.col("100_7")).to_series().to_list())))

159232

In [277]:
def hezkejmeno(sto):
    if not sto[-1].isalnum():
        sto = sto[:-1]
    if "," in sto:
        sto = sto.split(",")
        sto = sto[1].strip() + " " + sto[0].strip()
    return sto    

In [232]:
df = df.with_columns(pl.col("100_a").map_elements(hezkejmeno).alias("jméno"))

C:\Users\micha\AppData\Local\Temp\ipykernel_17068\2345623490.py:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
  df = df.with_columns(pl.col("100_a").map_elements(hezkejmeno).alias("jméno"))


In [233]:
df.group_by("jméno").len().sort(by="len",descending=True).head(11)

shape: (11, 2)
┌─────────────────────────┬─────┐
│ jméno                   ┆ len │
│ ---                     ┆ --- │
│ str                     ┆ u32 │
╞═════════════════════════╪═════╡
│ Jiří Vedral             ┆ 726 │
│ Božena Němcová          ┆ 308 │
│ Jan Amos Komenský       ┆ 296 │
│ Alexandr Batěk          ┆ 262 │
│ Josef Šváb-Malostranský ┆ 260 │
│ Zuzana Pospíšilová      ┆ 253 │
│ Tomáš Garrigue Masaryk  ┆ 247 │
│ Jan Neruda              ┆ 245 │
│ Jaroslav Vrchlický      ┆ 240 │
│ Karel Čapek             ┆ 227 │
│ Jaroslav Kříženecký     ┆ 218 │
└─────────────────────────┴─────┘

In [234]:
hvezdy = df.group_by("jméno").len().sort(by="len",descending=True).head(10).select(pl.col("jméno")).to_series().to_list()
hvezdy

['Jiří Vedral',
 'Božena Němcová',
 'Jan Amos Komenský',
 'Alexandr Batěk',
 'Josef Šváb-Malostranský',
 'Zuzana Pospíšilová',
 'Tomáš Garrigue Masaryk',
 'Jan Neruda',
 'Jaroslav Vrchlický',
 'Karel Čapek']

In [235]:
import datetime

In [236]:
do_grafu = df.filter(pl.col("jméno").is_in(hvezdy)).with_columns(pl.col("rok").map_elements(lambda x: datetime.date(year=int(x), month=1, day=1), return_dtype=pl.Date).cast(pl.Datetime))

In [237]:
y_encoding = {
        'field': 'jméno',
        'type': 'nominal',
        'title': None,
        'sort': hvezdy
    }

In [238]:
import altair as alt

In [239]:
def irozhlas_conf():

    return {
        "config" : {
             "title": {'font': "Noticia Text",
                      'fontSize': 14,
                      'anchor': 'start',
                       'fontWeight': 'bolder',
                    'subtitleFont': 'Noticia Text',
                      'subtitleFontSize': 12,
                       'subtitleFontWeight': 'lighter',
                      'subtitlePadding': 12,
                       'dy': -12,
                      },
             "axis": {
                "labelFont": "Asap",
                "titleFont": "Asap",
                 "fontWeight": "lighter",
                "titleFontWeight": "lighter",
                "labelFontSize": 10,
                "titleFontSize": 10,
                'labelPadding': 2,
                 'titlePadding': 10
            },
            "legend": {
                "labelFont": "Asap",
                "labelFontWeight": "normal",
                "titleFont": "Asap",
                "titleFontWeight": "normal",
                "labelFontSize": 10,
                "titleFontSize": 10
            }
        }
    }

alt.themes.register('irozhlas', irozhlas_conf)
alt.themes.enable('irozhlas')

ThemeRegistry.enable('irozhlas')

In [240]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [241]:
len(do_grafu)

3064

In [242]:
zebricek = alt.Chart(do_grafu.to_pandas(), title=alt.TitleParams(f"{len(hvezdy)} nejvydávanějších autorů a autorek (bez reprintů)"), width=300).mark_circle(size=8) \
        .encode(
            x=alt.X("rok:T", title=None, axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')), 
            y=alt.Y("jméno:N", sort=hvezdy, title=None, axis=alt.Axis(orient='left', domainOpacity=0, tickColor='#DCDDD6')), 
            yOffset=alt.YOffset("jitter:Q", scale=alt.Scale(range=[3, 15])), 
            color=alt.Color('jméno:N', scale=alt.Scale(range=['#D6534B', '#445B78', '#DB842F', '#70871E']), 
                            sort=hvezdy).legend(None)) \
        .transform_calculate(jitter="sqrt(-2*log(random()))*cos(2*PI*random())").configure_view(stroke='transparent')

zebricek

C:\Users\micha\anaconda3\Lib\site-packages\altair\utils\core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
C:\Users\micha\anaconda3\Lib\site-packages\altair\utils\core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
C:\Users\micha\anaconda3\Lib\site-packages\altair\utils\core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
C:\Users\micha\anaconda3\Lib\site-packages\altair\utils\core.

alt.Chart(...)

In [243]:
import json

In [275]:
df.filter(pl.col("100_a") == "Vedral, Jiří,").select(pl.col("stran")).sample(20)

shape: (20, 1)
┌───────┐
│ stran │
│ ---   │
│ i64   │
╞═══════╡
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
│ null  │
└───────┘

In [244]:
vedral = df.filter(pl.col("100_a") == "Vedral, Jiří,").select(pl.col("245_a")).to_series().to_list()
vedral

['Estonsko-český slovník CPA Toodete ja teenuste klassifikaator 2008',
 'Švédsko-český slovník jmen ptáků',
 'Německo-český přírodovědný slovník na CD',
 'Anglicko-český slovník kamenoprůmyslu',
 'Česko-anglický slovník jmen plazů',
 'Francúzsko-slovenský slovník subjadrová fyzika na CD',
 'Španělsko-český biologický slovník',
 'Švédsko-český slovník veřejných zakázek (CPV)',
 'Korejsko-český kosmetický slovník na CD',
 'Švédsko-český celní sazebník',
 'Anglicko-český slovník jmen měkkýšů',
 'Chorvatsko-český katalog odpadů',
 'Švédsko-český slovník ekonomických činností (NACE)',
 'Thajsko-český slovník International Standard Classification of Occupations (ISCO)',
 'Ázerbajdžánsko-český slovník PRODCOM',
 'Anglicko-český slovník dopravní',
 'Česko-německý slovník jmen motýlů',
 'Estonsko-český lékařský slovník',
 'Norsko-český lékařský slovník',
 'Česko-anglický lékařský slovník na CD',
 'Německo-český slovník životního prostředí',
 'Slovensko-český slovník jmen ptáků',
 'Anglicko-česk

In [245]:
with open(os.path.join("data_raw","vedral.json"), "w+", encoding="utf-8") as v:
    v.write(json.dumps(vedral))